In [1]:
import numpy as np
import scipy as sp
import scipy.signal
import matplotlib
import matplotlib.pyplot as plt
# you may need to first run conda install plotly
import plotly
import plotly.graph_objects as go

# Dynamic Estimation 2: non-linear processes

### Myles Allen

##### myles.allen@physics.ox.ac.uk

These we linearise, remembering that the Kalman formalism applies to perturbations about the reference trajectory, and $\mathbf{A}$ and $\mathbf{B}$ are now state-dependent:
$$ \delta \mathbf{x}_{t+\delta t} = \mathbf{A}(\mathbf{x}_{t})\delta \mathbf{x}_{t} + \mathbf{B}(\mathbf{x}_{t}) \mathbf{z}_{t} \quad .$$

$\mathbf{A}(\mathbf{x}_{t})$ is known as the "instantaneous linear error propagator":
$$ \mathbf{A}(\mathbf{x}_{t}) = \mathbf{I} + \mathbf{J}(\mathbf{x}_{t})\delta t$$

where $\mathbf{J}$ is the Jacobian. 

This works even for deterministic systems if we think of $\mathbf{B}$ as describing not just the accumulated impact of stochastic forcing, but the evolution of a small cloud of points under the governing equations. We can even model the evolution of such a cloud explicitly, which is the principle behind the so-called Ensemble Kalman Filter.


### Suppose we don't have synchronous observations... 

but instead observations come in continuously over some interval (a 12-hour assimilation cycle, for example), how do we find the initial conditions for the model that minimises the model-data misfit to all these observations?  Let's focus on the situation in which $\mathbf{S}_a = \mathbf{I}_n$, $\mathbf{S}_{\mathbf{u}} = \mathbf{I}_m$ and $\mathbf{x}_a = \mathbf{0}$. 

The optimal estimator becomes:
$$ \hat{\mathbf{x}} = \mathbf{H}^T (\mathbf{H}^T \mathbf{H} + \mathbf{I})^{-1} \mathbf{y} $$
where $\mathbf{H}$ is the linear
operator that predicts the observable quantities $\mathbf{y}$ from 
initial conditions $\mathbf{x}$.  If $\mathbf{x}$ and $\mathbf{y}$ are 
$10^7$-dimensional vectors, we can't write down $\mathbf{H}$ as a
simple matrix, but we can express it as an operator, in terms
of the weather model itself.  

But what about $\mathbf{H}^T$?

### Adjoint modelling

Recall the vector differentiation result
$$ \frac{\partial \mathbf{H} \mathbf{x}}{\partial \mathbf{x}} = \mathbf{H}^T $$
so $\mathbf{H}^T$ is simply the linear sensitivity of the predicted observations $\mathbf{H} \mathbf{x}$ 
to the "control variables" $\mathbf{x}$.  

When we have a non-linear model, we linearise the model equations about a reference trajectory: $\mathbf{H}^T$ then corresponds to an operator which involves running the linearised model backwards in time to compute the sensitivities of $\mathbf{H} \mathbf{x}$ to $\mathbf{x}$. This is known as "adjoint modelling". Running a model backwards in time sounds mysterious, but it is nothing more than the reversal of the order of multiplication under the transpose.


### Singular vectors

Expressing $\mathbf{A}$ in terms of its singular value decomposition $$\mathbf{A} = \mathbf{P} \mathbf{Q} \mathbf{R}^T , $$where $\mathbf{P}$ and $\mathbf{R}$ are orthonormal matrices and $\mathbf{Q}$ is diagonal, provides lots of information about the impact of observations and the evolution of errors.  

The left singular vectors (columns of $\mathbf{P}$) corresponding to the largest elements of $\mathbf{Q}$ are the dominant errors at time $t+\delta t$, while the corresponding right singular vectors (rows of $\mathbf{R}^T$) correspond to the critical errors in initial conditions that evolve into these dominant errors. 

$\mathbf{P}$ and $\mathbf{R}$ are the eigenvectors of $\mathbf{A}\mathbf{A}^T$ and 
$\mathbf{A}^T\mathbf{A}$ respectively.  This allows them to be calculated 
from the forward and adjoint linearised models even if we cannot
perform an explicit SVD of $\mathbf{A}$.

### Interpreting singular vectors over very small time intervals

If $\mathbf{H} = \mathbf{A}$ (complete observations) and $\delta t$ is small, then we have:
$$ \mathbf{H}^T \mathbf{H} = \mathbf{A}^T \mathbf{A} = (\mathbf{I} + \mathbf{J}\delta t)^T (\mathbf{I} + \mathbf{J}\delta t) = \mathbf{I} + (\mathbf{J} + \mathbf{J}^T)\delta t + \mbox{O}(\delta t^2)$$
and similarly for $\mathbf{H} \mathbf{H}^T$. So the left and right singular vectors are now identical: rotation of 
errors is an $\mbox{O}(\delta t^2)$ effect. They are also the eigenvectors of $(\mathbf{J} + \mathbf{J}^T)$, which is symmetric.

### Reducing errors in analysis and forecast

If our observations $\mathbf{y}$ are noisy, we can exploit knowledge of the system dynamics encapsulated in $\mathbf{A}$ to improve our optimal estimate $\hat{\mathbf{y}}=\mathbf{H}\hat{\mathbf{x}}$: 

In the special case that $\mathbf{S}_a = \mathbf{I}_n$, $\mathbf{H}=\mathbf{A}$ and $\mathbf{S}_{\mathbf{u}} = \mathbf{I}_m$ (complete observations with equal and uncorrelated errors in all elements of both observations and first guess), we have:

\begin{eqnarray*} \langle\hat{\mathbf{y}} \hat{\mathbf{y}}^T \rangle & = & \mathbf{H} (\mathbf{H}^T \mathbf{H} + \mathbf{I})^{-1} \mathbf{H}^T \\
& = & \mathbf{P} \mathbf{Q} \mathbf{R}^T \mathbf{R} (\mathbf{Q}^2+\mathbf{I})^{-1} \mathbf{R}^T \mathbf{R} \mathbf{Q} \mathbf{P}^T \\
& = & \mathbf{P} \mathbf{Q}^2 (\mathbf{Q}^2+\mathbf{I})^{-1} \mathbf{P}^T \end{eqnarray*}
So the errors in the $i^{th}$ pattern $\mathbf{p}_i$ has variance $q_i^2/(1+q_i^2)$:
if $q_i \ll 1$, so perturbations contract, then
the error in the optimal estimate is small in that direction.

### Adaptive observation systems

If we have a limited
number of observations to make at time $t+\delta t$ then we 
minimise the uncertainty in the estimate of the initial state $\hat{\mathbf{x}}$, 
$$ \langle \hat{\mathbf{x}} \hat{\mathbf{x}}^T \rangle = (\mathbf{H}^T \mathbf{H} + \mathbf{I})^{-1} = \mathbf{R} (\mathbf{Q}^2+\mathbf{I})^{-1} \mathbf{R}^T , $$
by aligning these observations
with the dominant singular vectors of $\mathbf{A}$.  Where these 
observations are required depends on the trajectory the equations
have been linearised about: "flow-dependent" errors.  

This method is being used to target observations onto
evolving storms as they develop in mid-ocean a few days before
they arrive into inhabited regions.

### Error growth in the Lorenz '63 system
The Lorenz system consists of the following set of three equations:
$$
\begin{align}
\dot{x} & = \sigma(y-x) \\
\dot{y} & = \rho x - y - xz \\
\dot{z} & = -\beta z + xy
\end{align}
$$

In [2]:
## define the Lorenz '63 system:
def L63(X, t, r, s, b):
    x, y, z = X  # Unpack the state vector
    return s * (y - x), x * (r - z) - y, x * y - b * z
## define the Lorenz '63 Jacobian:
def L63_J(X, r, s, b):
    x, y, z = X  # Unpack the state vector
    return np.array([ [ -s , s , 0 ],[ r - z , -1 , -x ],[ y , x , -b ] ])
## Specify model parameters:
s, r, b = [10, 28, 8/3]
## Specify integration time and timestep:
dt = 0.01
int_time = 100.
t = np.arange( 0 , int_time , dt )
I = np.identity(3)
## Specify initial conditions
X0 = [0.1 , 0.1 , 5]

In [3]:
## integrate the model using scipy's odeint:
X = sp.integrate.odeint(L63, X0, t, args=(r,s,b))
J = np.array([L63_J(X[i], r, s, b) for i in np.arange(t.size)])
A_i = J*dt+I
# Calculate time-evolving SVD of instantaneous error propagator A_i
P, Q, Rt = np.linalg.svd(A_i)
ly0=Q[:,0]
print("Instantaneous error growth rates in the Lorenz system")
fig = go.Figure( data=[ go.Scatter3d(x=X[:,0],y=X[:,1],z=X[:,2], mode='lines', line=dict(colorscale='magma',color=ly0)) ] )
fig.update_layout(scene = dict(xaxis = dict(showbackground=False,zerolinecolor="grey",range=[-25,25]),yaxis = dict(showbackground=False,zerolinecolor="grey",range=[-30,30]),zaxis = dict(showbackground=False,zerolinecolor="grey",range=[0,55]),),width=900,height=900,margin=dict(r=10, l=10, b=10, t=10), showlegend=False)
fig.show()

Instantaneous error growth rates in the Lorenz system


### A puzzle

Why do errors seem to grow fastest after the trajectory has left the bottom of the central divergence region (recall it moves downwards near the $z$-axis)?

### Propagation of errors over a finite time

If the observations $\mathbf{y}$ provide a complete description of the state of the system at time $t+n\delta t$, where $n\delta t$ is a finite time-interval, then $\mathbf{H}$ is the linear operator that takes a perturbation to the initial conditions, $\mathbf{x}_t$, into
a change of state at the time of the observation, $\mathbf{x}_{t+n\delta t}$. Under these conditions
$$ \mathbf{H} = \mathbf{A}(t \ldots t+n\delta t) = \mathbf{A}(\mathbf{x}_{t+n\delta t})\mathbf{A}(\mathbf{x}_{t+(n-1)\delta t})\ldots\mathbf{A}(\mathbf{x}_{t+\delta t})\mathbf{A}(\mathbf{x}_{t})  . $$

The linear error propagator $\mathbf{A}$, whether instantaneous or not, is always square, but $\mathbf{H}$ need not be if observations are incomplete or if observations come in over a sequence of time-intervals. Note how the time-ordering is reversed in the construction of $\mathbf{H}^T$: when we can't calculate compute $\mathbf{A}$ explicitly, operations involving $\mathbf{H}^T$ require running the adjoint model backwards in time.

In [4]:
# Calculate finite-time error propagation over a time-window size t_s in Lorenz "days"
t_s = 0.5
n_s = int(t_s/dt)
A_s = np.zeros_like(A_i)
for i in range(0, t.size - n_s):
    A_s[i,:,:] = A_i[i,:,:]
    for j in range(1, min(n_s,t.size-1-i)):
        A_s[i,:,:] = A_i[i+j,:,:]@A_s[i,:,:] # the product of instantaneous error propagators over time interval
P, Q, Rt = np.linalg.svd(A_s)
ly0=Q[:,0]
ly1=np.zeros_like(ly0)
ly1[n_s:]=ly0[:t.size-n_s]

In [5]:
lyp=ly0 # plot ly0 for growth rate as a function of initial time, ly1 as a function of final time
print("Half-day error growth rates in the Lorenz system: forecast initialisation time")
fig = go.Figure( data=[ go.Scatter3d(x=X[:,0],y=X[:,1],z=X[:,2], mode='lines', line=dict(colorscale='magma',color=lyp)) ] )
fig.update_layout(scene = dict(xaxis = dict(showbackground=False,zerolinecolor="grey",range=[-25,25]),yaxis = dict(showbackground=False,zerolinecolor="grey",range=[-30,30]),zaxis = dict(showbackground=False,zerolinecolor="grey",range=[-20,55]),),width=900,height=900,margin=dict(r=10, l=10, b=10, t=10), showlegend=False)
fig.show()

Half-day error growth rates in the Lorenz system: forecast initialisation time


In [6]:
lyp=ly1 # plot ly0 for growth rate as a function of initial time, ly1 as a function of final time
print("Half-day error growth rates in the Lorenz system: forecast verification time")
fig = go.Figure( data=[ go.Scatter3d(x=X[:,0],y=X[:,1],z=X[:,2], mode='lines', line=dict(colorscale='magma',color=lyp)) ] )
fig.update_layout(scene = dict(xaxis = dict(showbackground=False,zerolinecolor="grey",range=[-25,25]),yaxis = dict(showbackground=False,zerolinecolor="grey",range=[-30,30]),zaxis = dict(showbackground=False,zerolinecolor="grey",range=[-20,55]),),width=900,height=900,margin=dict(r=10, l=10, b=10, t=10), showlegend=False)
fig.show()

Half-day error growth rates in the Lorenz system: forecast verification time
